# 降噪

In [7]:
import os
import librosa
import noisereduce as nr
import soundfile as sf

input_dir = r"./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio"
output_dir = r"./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio_clean"
os.makedirs(output_dir, exist_ok=True)

for filename in os.listdir(input_dir):
    if filename.endswith(".wav"):
        input_path = os.path.join(input_dir, filename)
        output_path = os.path.join(output_dir, filename)

        # 載入音訊
        y, sr = librosa.load(input_path, sr=None)  # 保留原始取樣率

        # 自動估計靜音段作為 noise sample
        noise_sample = y[0:int(sr * 0.5)] if len(y) > sr else y  # 前 0.5 秒當作雜訊樣本

        # 降噪
        reduced_noise = nr.reduce_noise(y=y, sr=sr, y_noise=noise_sample)

        # 儲存降噪後音檔
        sf.write(output_path, reduced_noise, sr)

        print(f"已處理並儲存：{output_path}")


已處理並儲存：./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio_clean\24016.wav
已處理並儲存：./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio_clean\24018.wav
已處理並儲存：./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio_clean\24023.wav
已處理並儲存：./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio_clean\24055.wav
已處理並儲存：./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio_clean\24063.wav
已處理並儲存：./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio_clean\24081.wav
已處理並儲存：./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio_clean\24098.wav
已處理並儲存：./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio_clean\24198.wav
已處理並儲存：./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio_clean\24224.wav
已處理並儲存：./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio_clean\2423.wav
已處理並儲存：./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio_clean\24244.wav
已處理並儲存：./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio_clean\242

# Task 1

In [ ]:
# !pip install  datasets evaluate jiwer librosa
# !pip install --upgrade bitsandbytes transformers==4.50.0 accelerate

## Imoprt package

In [ ]:
# from google.colab import drive
# drive.mount('/content/drive')

MessageError: Error: credential propagation was unsuccessful

In [3]:
import os
import shutil

# 刪除 __pycache__ 資料夾
shutil.rmtree('__pycache__', ignore_errors=True)


In [17]:
import os
import sys
import json
import torch
import random
import librosa
import zipfile
import evaluate
import numpy as np
import pandas as pd
from datasets import Dataset, Audio, load_dataset, Features, Value
from aicup import (DataCollatorSpeechSeq2SeqWithPadding,
      transcribe_with_timestamps,
      collate_batch_with_prompt_template,
      generate_annotated_audio_transcribe_parallel,OpenDeidBatchSampler)
from transformers import (
    WhisperFeatureExtractor, WhisperTokenizer, WhisperProcessor,
    WhisperForConditionalGeneration, Seq2SeqTrainingArguments, Seq2SeqTrainer, AutoTokenizer
)

## Download audio file

In [2]:
zip_path = "TRAINGING DATASET_1PHASE-001.zip"
extract_dir = "audio_dataset"
os.makedirs(extract_dir, exist_ok=True)

with zipfile.ZipFile(zip_path, 'r') as zip_ref:
  zip_ref.extractall(extract_dir)

audio_files = []
for root, dirs, files in os.walk(extract_dir):
  for file in files:
    if file.lower().endswith('.wav'):
      audio_files.append(os.path.join(root, file))

print(f"found {len(audio_files)} audio files")
# for path in audio_files:
#   print(path)

found 1517 audio files


In [2]:
def set_torch_seed(seed=0):
  random.seed(seed)
  np.random.seed(seed)
  torch.manual_seed(seed)
  torch.backends.cudnn.deterministic = True
  torch.backends.cudnn.benckmark = False
  if torch.cuda.is_available():
    torch.cuda.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
set_torch_seed()

In [2]:
t1_train_audio_folder = r"./audio_dataset/TRAINGING_DATASET_1/Training_Dataset_01/audio_clean"
t1_train_transcription_file = r"./audio_dataset/TRAINGING_DATASET_1/Training_Dataset_01/task1_answer.txt"
transcripts, dataset_list = {}, []

with open(t1_train_transcription_file, "r", encoding="utf-8") as f:
  for line in f:
    if line.strip():
      parts = line.strip().split("\t", 1)
      if len(parts) == 2:
        filename, transcript = parts
        transcripts[filename] = transcript

for file in sorted(os.listdir(t1_train_audio_folder)):
  if file.endswith(".wav") and file.split(".")[0] in transcripts:
    try:
      file_path = os.path.join(t1_train_audio_folder, file)
      audio_array, sr = librosa.load(file_path, sr=16000)
      dataset_list.append({"audio":
                 {
                  "path":file_path,
                  "array":audio_array,
                  "sampling_rate":sr
                 },
                 "sentence": transcripts[file.split(".")[0]]})
    except Exception as e:
      print(e)
      print(f"Can't read {file_path}:{e}")

dataset = Dataset.from_pandas(pd.DataFrame(dataset_list))

In [3]:
dataset[0]['audio']['array'][:20]

[-7.05636921338737e-07,
 -2.0444844267331064e-05,
 -1.6001751646399498e-05,
 -1.30140979308635e-05,
 -2.573244273662567e-05,
 -1.8088117940351367e-05,
 -2.160936128348112e-05,
 -1.976025669137016e-05,
 -9.819679689826444e-06,
 -1.6359928849851713e-05,
 -2.2137146515888162e-05,
 -1.8998798623215407e-05,
 -2.188768849009648e-05,
 -1.3655586371896788e-05,
 -7.867609383538365e-06,
 -1.794035779312253e-05,
 -2.0494968339335173e-05,
 -2.1314823243301362e-05,
 -1.3494478480424732e-05,
 -1.927842095028609e-05]

In [4]:
print("audio sample:",len(dataset[0]['audio']['array']))
print("audio duration:",len(dataset[0]['audio']['array'])/16000)

audio sample: 375968
audio duration: 23.498


In [5]:
split_ratio = 0.8
train_size = int(len(dataset) * split_ratio)
dataset = dataset.train_test_split(train_size=train_size,
     test_size=len(dataset) - train_size, shuffle=True, seed=42)
train_dataset = dataset["train"]
test_dataset = dataset["test"]

print(f"Train: {len(train_dataset)} samples, Test: {len(test_dataset)} samples")

Train: 1231 samples, Test: 308 samples


In [6]:
test_dataset[0]

{'audio': {'array': [-2.9569491744041443e-05,
   -6.516207940876484e-05,
   -5.389004945755005e-05,
   -4.562793765217066e-05,
   -4.769768565893173e-05,
   -4.169507883489132e-05,
   -6.482354365289211e-05,
   -4.023849032819271e-05,
   -2.826540730893612e-05,
   -3.165693487972021e-05,
   -2.999464049935341e-05,
   -3.0357507057487965e-05,
   -3.199535422027111e-05,
   -1.0943738743662834e-05,
   3.018416464328766e-06,
   -1.7094425857067108e-06,
   1.0725343599915504e-06,
   -6.243353709578514e-07,
   2.3422762751579285e-07,
   1.6763806343078613e-07,
   -7.255584932863712e-07,
   2.550543285906315e-06,
   2.7369358576834202e-05,
   3.3503398299217224e-05,
   9.69856046140194e-06,
   -1.912703737616539e-06,
   6.882473826408386e-07,
   -1.3154931366443634e-08,
   -1.7343554645776749e-06,
   -1.7360900528728962e-05,
   -7.033813744783401e-07,
   -1.8572667613625526e-05,
   -3.481539897620678e-05,
   -2.676231088116765e-05,
   -3.631832078099251e-05,
   -3.765523433685303e-05,
   -2.9

## Model import

In [5]:
from transformers import AutoTokenizer
model_name = "openai/whisper-large-v3-turbo"#"openai/whisper-medium"  #"small", "medium", "large"

tokenizer = AutoTokenizer.from_pretrained(model_name)
tokenizer.save_pretrained("./model_result/task1/v1/model/fine-tuning-whisper")


('./model_result/task1/v1/model/fine-tuning-whisper\\tokenizer_config.json',
 './model_result/task1/v1/model/fine-tuning-whisper\\special_tokens_map.json',
 './model_result/task1/v1/model/fine-tuning-whisper\\vocab.json',
 './model_result/task1/v1/model/fine-tuning-whisper\\merges.txt',
 './model_result/task1/v1/model/fine-tuning-whisper\\normalizer.json',
 './model_result/task1/v1/model/fine-tuning-whisper\\added_tokens.json',
 './model_result/task1/v1/model/fine-tuning-whisper\\tokenizer.json')

In [3]:
model_name = "openai/whisper-large-v3-turbo"#"openai/whisper-medium"  #"small", "medium", "large"
feature_extractor = WhisperFeatureExtractor.from_pretrained(model_name)
tokenizer = WhisperTokenizer.from_pretrained(model_name)
tokenizer.padding_side = 'left'
processor = WhisperProcessor.from_pretrained(model_name)
model = WhisperForConditionalGeneration.from_pretrained(model_name)
model.generation_config.language = None
model.generation_config.task = "transcribe"
model.generation_config.forced_decoder_ids = None

### Pre-evaluate

In [59]:
from jiwer import mer
from transformers.models.whisper.english_normalizer import BasicTextNormalizer


def calculate_mer(ground_truth_texts, predicted_texts):
  """ Mix Error Rate (MER) English only"""
  mer_scores = {}
  total_mer = 0
  count = 0

  normalizer = BasicTextNormalizer()

  for filename, ref_text in ground_truth_texts.items():
    if filename in predicted_texts:
      pred_text = predicted_texts[filename]
      ref_text = normalizer(ref_text)
      pred_text = normalizer(pred_text)
      mer_score = mer(ref_text, pred_text)
      mer_scores[filename] = mer_score
      total_mer += mer_score
    else:
      mer_scores[filename] = 1
      total_mer += 1
    count += 1

  average_mer = total_mer / count if count != 0 else 0
  return mer_scores, average_mer

def evaluate_mer(model, processor, dataset):
  predictions = {}
  references = {}

  for sample in dataset:
    filename = sample["audio"]["path"].split("/")[-1].split(".")[0]
    audio_array = sample['audio']['array']
    sr = sample['audio']['sampling_rate']
    input_features = processor.feature_extractor(
        audio_array,
        sampling_rate=sr,
        return_tensors="pt"
    ).input_features.to(model.device)
    with torch.no_grad():
      predicted_ids = model.generate(input_features)
      transcription = processor.tokenizer.batch_decode(predicted_ids, skip_special_tokens=True)[0].strip()

    predictions[filename] = transcription
    references[filename] = sample["sentence"].strip()

  mer_scores, avg_mer = calculate_mer(references, predictions)
  return mer_scores, avg_mer, predictions, references

In [5]:
import torch
print(torch.cuda.is_available())  # 如果返回 True，則表示 PyTorch 能夠識別 CUDA 並使用 GPU
print(torch.cuda.get_device_name(0))  # 顯示當前使用的 GPU 名稱


True
NVIDIA GeForce RTX 5080


In [9]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = model.to(device)


In [16]:
mer_scores, avg_mer, predictions, references = evaluate_mer(model, processor, test_dataset)
print("All mer scores:\n",mer_scores)
print("Average mer scores:\n",avg_mer)
print("Predict :\n",predictions)
print("Answer :\n",references)

Passing a tuple of `past_key_values` is deprecated and will be removed in Transformers v4.43.0. You should pass an instance of `EncoderDecoderCache` instead, e.g. `past_key_values=EncoderDecoderCache.from_legacy_cache(past_key_values)`.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


All mer scores:
 {'audio\\14137': 0.03571428571428571, 'audio\\16159': 0.024390243902439025, 'audio\\81228': 1.0, 'audio\\13240': 0.11764705882352941, 'audio\\18098': 0.05263157894736842, 'audio\\36127': 0.01639344262295082, 'audio\\37724': 0.0, 'audio\\54856': 0.03571428571428571, 'audio\\15599': 0.06060606060606061, 'audio\\12309': 0.03333333333333333, 'audio\\37013': 0.04918032786885246, 'audio\\18397': 0.012345679012345678, 'audio\\40211': 0.018518518518518517, 'audio\\41350': 0.05172413793103448, 'audio\\54877': 0.6296296296296297, 'audio\\40959': 0.0, 'audio\\33239': 0.05714285714285714, 'audio\\40092': 0.0, 'audio\\3984': 0.25, 'audio\\43017': 0.06896551724137931, 'audio\\54219': 0.0, 'audio\\82664': 1.0, 'audio\\35652': 0.037037037037037035, 'audio\\43638': 0.027777777777777776, 'audio\\37083': 0.014084507042253521, 'audio\\80009': 1.0, 'audio\\38179': 0.08974358974358974, 'audio\\23991': 0.0, 'audio\\22216': 0.07692307692307693, 'audio\\41165': 0.05263157894736842, 'audio\\162

## Dataset

In [66]:
# print(processor.feature_extractor(test_dataset[2]['audio']['array'],
#     sampling_rate=test_dataset[2]['audio']["sampling_rate"])['input_features'])
print(tokenizer(test_dataset[2]['sentence']).input_ids)

KeyError: 'sentence'

In [62]:
def preprocess_dataset(batch):

  audio = batch["audio"]
  batch["input_features"] = processor.feature_extractor(audio["array"],
    sampling_rate=audio["sampling_rate"]).input_features[0]
  batch["labels"] = tokenizer(batch["sentence"]).input_ids

  return batch

train_dataset = train_dataset.map(preprocess_dataset, remove_columns=dataset.column_names["train"]) #,num_proc=4
test_dataset = test_dataset.map(preprocess_dataset, remove_columns=dataset.column_names["test"])

ValueError: Column to remove ['sentence', 'audio'] not in the dataset. Current columns in the dataset: ['input_features', 'labels']

In [18]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(
    processor=processor,
    decoder_start_token_id=model.config.decoder_start_token_id,
)

In [19]:
d = [test_dataset[i] for i in range(2)]
batch = data_collator(d)
print(batch['input_features'])
print(batch['labels'])

tensor([[[-0.6399, -0.7049, -0.6500,  ..., -0.7349, -0.7349, -0.7349],
         [-0.5423, -0.6073, -0.5525,  ..., -0.7349, -0.7349, -0.7349],
         [-0.5489, -0.6883, -0.3071,  ..., -0.7349, -0.7349, -0.7349],
         ...,
         [-0.7349, -0.7349, -0.7349,  ..., -0.7349, -0.7349, -0.7349],
         [-0.7349, -0.7349, -0.7349,  ..., -0.7349, -0.7349, -0.7349],
         [-0.7349, -0.7349, -0.7349,  ..., -0.7349, -0.7349, -0.7349]],

        [[-0.7853, -0.7853, -0.7853,  ..., -0.7853, -0.7853, -0.7853],
         [-0.7853, -0.7853, -0.7853,  ..., -0.7853, -0.7853, -0.7853],
         [-0.7853, -0.7853, -0.7853,  ..., -0.7853, -0.7853, -0.7853],
         ...,
         [-0.7853, -0.7853, -0.7853,  ..., -0.7853, -0.7853, -0.7853],
         [-0.7853, -0.7853, -0.7853,  ..., -0.7853, -0.7853, -0.7853],
         [-0.7853, -0.7853, -0.7853,  ..., -0.7853, -0.7853, -0.7853]]])
tensor([[50364,   474,  1578,   466,   406,  1419,  1096,   309,   293,   286,
           841,  6884,   293,   300, 

In [20]:
from jiwer import mer
from transformers.models.whisper.english_normalizer import BasicTextNormalizer


normalizer = BasicTextNormalizer()

def mixed_tokenizer(text):
  text = normalizer(text.strip())
  tokens = []
  temp_token = ""
  # print(text)
  for char in text:
    if '\u4e00' <= char <= '\u9fff':
      if temp_token:
          tokens.append(temp_token)
          temp_token = ""
      tokens.append(char)
    elif char.isspace():
      if temp_token:
        tokens.append(temp_token)
        temp_token = ""
    else:
      temp_token += char
  if temp_token:
    tokens.append(temp_token)
  return tokens

def compute_metrics(eval_pred):
  predictions, labels = eval_pred

  decoded_preds = processor.batch_decode(predictions, skip_special_tokens=True)
  decoded_labels = processor.batch_decode(labels, skip_special_tokens=True)

  decoded_preds = [normalizer(pred.strip()) for pred in decoded_preds]
  decoded_labels = [normalizer(label.strip()) for label in decoded_labels]

  paired = [
      (ref, hyp) for ref, hyp in zip(decoded_labels, decoded_preds)
      if ref.strip() != "" and hyp.strip() != ""
  ]

  filtered_labels, filtered_preds = zip(*paired) if paired else ([], [])
  if len(filtered_labels) == 0:
    return {"mer": 1.0}

  ref_tokens = [mixed_tokenizer(t) for t in filtered_labels]
  pred_tokens = [mixed_tokenizer(t) for t in filtered_preds]
  # print(ref_tokens)
  # print(pred_tokens)
  ref_strs = [" ".join(tokens) for tokens in ref_tokens]
  pred_strs = [" ".join(tokens) for tokens in pred_tokens]

  try:
    score = mer(ref_strs, pred_strs)
  except Exception as e:
    print("Error during MER computation:", e)
    score = 1.0

  return {"mer": score}

## Finetune decoder only (option)

In [21]:
for param in model.model.encoder.parameters():
  param.requires_grad = False

In [22]:
trainable_params = sum(p.numel() for p in model.parameters() if p.requires_grad)
total_params = sum(p.numel() for p in model.parameters())

print(f"Trainable parameters: {trainable_params:,}")
print(f"Total parameters:     {total_params:,}")
print(f"Trainable ratio:      {trainable_params / total_params:.2%}")

Trainable parameters: 171,909,120
Total parameters:     808,878,080
Trainable ratio:      21.25%


## Training & args

In [23]:
train_dataset

Dataset({
    features: ['input_features', 'labels'],
    num_rows: 1231
})

In [28]:
training_args = Seq2SeqTrainingArguments(
  output_dir="/content/whisper-tiny/logs",
  report_to="none",
  num_train_epochs=5,
  per_device_train_batch_size=4,
  per_device_eval_batch_size=4,
  evaluation_strategy="epoch",
  save_strategy="epoch",
  predict_with_generate=True,
  logging_dir="/content/whisper-tiny/logs",
  logging_steps=1,
  fp16=True,
  learning_rate=1e-4,
  lr_scheduler_type="cosine",
  warmup_ratio=0.1,
  gradient_accumulation_steps=4,
  dataloader_num_workers=0,
)

trainer = Seq2SeqTrainer(
  model=model,
  args=training_args,
  train_dataset=train_dataset,
  eval_dataset=test_dataset,
  processing_class=processor,  # 使用 processor 代替 tokenizer
  data_collator=data_collator,
  compute_metrics=compute_metrics
)

In [29]:
trainer.train()

  0%|          | 0/385 [02:00<?, ?it/s]
Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x000001C0D174ADE0>
Traceback (most recent call last):
  File "c:\Users\mb205\anaconda3\envs\DataMining\Lib\site-packages\torch\utils\data\dataloader.py", line 1663, in __del__
    self._shutdown_workers()
  File "c:\Users\mb205\anaconda3\envs\DataMining\Lib\site-packages\torch\utils\data\dataloader.py", line 1621, in _shutdown_workers
    if self._persistent_workers or self._workers_status[worker_id]:
                                   ^^^^^^^^^^^^^^^^^^^^
AttributeError: '_MultiProcessingDataLoaderIter' object has no attribute '_workers_status'
                                               
  0%|          | 1/385 [00:02<17:53,  2.80s/it]

{'loss': 3.085, 'grad_norm': nan, 'learning_rate': 0.0, 'epoch': 0.01}


                                               
  1%|          | 2/385 [00:04<14:51,  2.33s/it]

{'loss': 4.6175, 'grad_norm': 52.79301452636719, 'learning_rate': 2.564102564102564e-06, 'epoch': 0.03}


                                               
  1%|          | 3/385 [00:06<13:36,  2.14s/it]

...

Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.

Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.

Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use 

{'eval_loss': 0.5595592856407166, 'eval_mer': 0.07130450273905492, 'eval_runtime': 160.141, 'eval_samples_per_second': 1.923, 'eval_steps_per_second': 0.481, 'epoch': 5.0}


                                                 
100%|██████████| 385/385 [26:18<00:00,  4.10s/it]

{'train_runtime': 1578.5442, 'train_samples_per_second': 3.899, 'train_steps_per_second': 0.244, 'train_loss': 0.8297697570610356, 'epoch': 5.0}


TrainOutput(global_step=385, training_loss=0.8297697570610356, metrics={'train_runtime': 1578.5442, 'train_samples_per_second': 3.899, 'train_steps_per_second': 0.244, 'total_flos': 1.04939743444992e+19, 'train_loss': 0.8297697570610356, 'epoch': 5.0})

In [4]:
save_directory = r"./models/whisper-large-v3-turbo-finetune"

model.save_pretrained(save_directory)
tokenizer.save_pretrained(save_directory)
processor.save_pretrained(save_directory)

print(f"Model saved to {save_directory}")

Model saved to ./models/whisper-large-v3-turbo-finetune


## postvalue

In [31]:
mer_scores, avg_mer, predictions, references = evaluate_mer(model, processor, test_dataset)
print("All mer scores:\n",mer_scores)
print("Average mer scores:\n",avg_mer)
print("Predict :\n",predictions)
print("Answer :\n",references)

KeyError: 'audio'

## Output result

In [3]:
valid_dataset_list = []
t1_vaild_audio_folder = r"./audio_dataset/TRAINGING_DATASET_1/Validation_Dataset/audio"
for file in sorted(os.listdir(t1_vaild_audio_folder)):
  if file.endswith(".wav"):
    try:
      file_path = os.path.join(t1_vaild_audio_folder, file)
      audio_array, sr = librosa.load(file_path, sr=16000)
      valid_dataset_list.append({"audio": {"path":file_path,'array':audio_array,'sampling_rate':sr},
                                 "sentence": ""})
    except Exception as e:
      print(e)
      print(f"Can't read {file_path}")

valid_dataset = Dataset.from_pandas(pd.DataFrame(valid_dataset_list))

In [4]:
valid_dataset

Dataset({
    features: ['audio', 'sentence'],
    num_rows: 775
})

In [ ]:
# model_name = "/content/drive/MyDrive/aicup/models/whisper-tiny"
# model = WhisperForConditionalGeneration.from_pretrained(model_name)
# processor = WhisperProcessor.from_pretrained(model_name)
model.generation_config.language = 'en'
model.to("cuda" if torch.cuda.is_available() else "cpu")
model.eval()

output_file = r"./result/TRAINGING DATASET_1PHASE/submission/task1_answer.txt"
json_output_file = r"./result/TRAINGING DATASET_1PHASE/task1_answer_timestamps.json"
_mapping = {}
with open(output_file, "w", encoding="utf-8") as f:
  for _file in valid_dataset:
    fileid = _file['audio']['path'].split("\\")[-1].split(".")[0]
    print(fileid)
    result = transcribe_with_timestamps(_file,model,processor)
    _mapping[fileid] = result
    f.write(f"{fileid}\t{result['text']}\n")
    
#with open(json_output_file, "w", encoding="utf-8") as f:
#  json.dump(_mapping, f, ensure_ascii=False)

The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


24016
24018
24023
24055
24063
24081
24098
24198
24224
2423
24244
24264
24274
24290
24293
24304
24333
24342
24346
24361
24366
24382
24387
24404
24428
24444
24460
24462
24542
24552
24597
24602
24613
24644
2465
24653
24675
24691
24760
24770
24772
24782
24823
24847
24850
2487
24899
24909
24912
2494
24947
24961
24976
25002
25010
25023
25024
25028
2505
25069
25077
25097
25115
25123
2515
25165
25176
25225
25237
25256
25273
25274
25286
25306
25309
25330
25344
25367
25369
25377
25390
25434
25457
25507
25516
25520
25527
2553
25533
25557
25581
25588
25598
2561
25685
25714
25724
25745
25770
25785
25790
25803
2582
2583
25837
2584
25853
25860
25864
25874
25909
25945
25952
25961
26021
26035
26041
26053
26054
26092
26095
26121
26151
26193
26197
26239
26248
26251
26273
26286
26290
26304
26305
26315
26359
26362
26392
26404
26406
26414
26432
2644
26523
26604
26631
26664
26665
26671
26698
26708
26725
26732
26754
26811
26830
26838
26845
26859
26860
26876
26877
26889
26946
2695
26965
26968
26998
27001
27057

# Task 2

In [1]:
import os
import sys
import json
import torch
import random
import librosa
import zipfile
import evaluate
import numpy as np
import pandas as pd
from datasets import Dataset, Audio, load_dataset, Features, Value
from aicup import (DataCollatorSpeechSeq2SeqWithPadding,
      transcribe_with_timestamps,
      collate_batch_with_prompt_template,
      clean_kv,
      generate_annotated_audio_transcribe_parallel,OpenDeidBatchSampler)
from transformers import (
    WhisperFeatureExtractor, WhisperTokenizer, WhisperProcessor,
    WhisperForConditionalGeneration, Seq2SeqTrainingArguments, Seq2SeqTrainer, AutoTokenizer
)

c:\Users\mb205\anaconda3\envs\DataMining\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [ ]:
task2_train_answer = r"./audio_dataset/TRAINGING_DATASET_1/Training_Dataset_01/task2_answer.txt"
task2_train_transcribe =  r"./audio_dataset/TRAINGING_DATASET_1/Training_Dataset_01/task1_answer.txt"
task2_train_data = r"./audio_dataset/TRAINGING_DATASET_1/Training_Dataset_01/task2_train.tsv"
generate_annotated_audio_transcribe_parallel(task2_train_answer, task2_train_transcribe, task2_train_data, num_processes=4)

process annotation file...
annotation file done
processing each medical file
1093	Alright, thank you. Ok can you stop it.	PHI:Null

1539
All medical file done
write out to tsv format...
tsv format dataset done


In [ ]:
# task2_train_answer_VAL = r"./audio_dataset/TRAINGING_DATASET_1/Training_Dataset_01/task2_answer_VAL.txt"
# task2_train_transcribe_VAL =  r"./audio_dataset/TRAINGING_DATASET_1/Training_Dataset_01/task1_answer_VAL.txt"
# task2_train_data_VAL = r"./audio_dataset/TRAINGING_DATASET_1/Training_Dataset_01/task2_train_VAL.tsv"
# generate_annotated_audio_transcribe_parallel(task2_train_answer_VAL, task2_train_transcribe_VAL, task2_train_data_VAL, num_processes=4)

process annotation file...
annotation file done
processing each medical file
2561	Yeah. But I've been dreading talking about it and it wasn't so bad, you know. Just about what we were going to do as far as selling, you know. And I said I was going to do something. Oh, see if they have an investment modification program. Maybe I'll call them today or tomorrow. This is the bank? Yeah. Just to buy some time, you know. My condo litigation is just I'm on all these emails that I can't even read them.	DATE:today\nDATE:tomorrow

775
All medical file done
write out to tsv format...
tsv format dataset done


In [123]:
task2_train_data = r"./audio_dataset/TRAINGING_DATASET_1/Training_Dataset_01/task2_train.tsv"


## Read dataset

In [124]:
from datasets import load_dataset, Features, Value

task2_data = load_dataset("csv",data_files=task2_train_data, delimiter='\t',
  features = Features({'fid': Value('string'),'content': Value('string'),'label':Value('string')}),
  column_names=['fid','content','label'])

Generating train split: 2307 examples [00:00, 70879.52 examples/s]


In [125]:
task2_data

DatasetDict({
    train: Dataset({
        features: ['fid', 'content', 'label'],
        num_rows: 2307
    })
})

In [126]:
from collections import Counter


ctr = Counter()

for i in task2_data['train']:
  phi_labelwvalue = i['label'].split("\\n")
  phi_label = [j.split(":")[0] for j in phi_labelwvalue]
  ctr.update(phi_label)

print(ctr)

Counter({'DATE': 1164, 'PHI': 863, 'DOCTOR': 534, 'DURATION': 486, 'PATIENT': 356, 'TIME': 281, 'PERSONALNAME': 240, 'ID_NUMBER': 235, 'FAMILYNAME': 174, 'HOSPITAL': 113, 'CITY': 112, 'DEPARTMENT': 106, 'MEDICAL_RECORD_NUMBER': 99, 'STATE': 98, 'STREET': 88, 'ZIP': 82, 'SET': 70, 'AGE': 56, 'PROFESSION': 40, 'ORGANIZATION': 31, 'LOCATION-OTHER': 25, 'COUNTRY': 11, 'DISTRICT': 3, 'COUNTY': 3, 'ROOM': 3, 'PHONE': 2, 'PROFSSION': 2, 'URL': 1})


In [6]:
count = 0
for item in task2_data['train']:
    if item['label'] == 'PHI:Null':
        count += 1

print(f"PHI:Null 樣本數量: {count}")
print(f"總樣本數量: {len(task2_data['train'])}")
print(f"有標註的樣本比例: {1 - count/len(task2_data['train']):.2%}")


PHI:Null 樣本數量: 628
總樣本數量: 1533
有標註的樣本比例: 59.03%


In [7]:
for item in task2_data['train']:
    print(item)

{'fid': '19', 'content': 'Any overture of something that\'s kind of like a little white flag or peace offering to just get a week of peace, I\'m not talking about permanent "I\'m going to placate and cow tow to you and to talk my needs in other..." No. Just talking about lets...', 'label': 'PHI:Null'}
{'fid': '23', 'content': "Yeah, I imagine it would — sorry, go ahead. So it's supposed to work immediately, right? Yep. So we'll see if I'm productive tomorrow. I hope I'm productive today. I've actually been trying to plan. If I do the titles today, then I can do my laundry tomorrow. Right. I probably could bring my computer and do titles while I'm doing my laundry. If I was — but I won't do that.", 'label': 'DATE:tomorrow\\nDATE:today\\nDATE:today\\nDATE:tomorrow'}
{'fid': '121', 'content': 'It makes it really hard when I lose things. Even this morning, he knocked over my glasses. I had them on the dresser and he was trying to find them this morning because I can\'t see anything without

In [9]:
from collections import Counter


ctr = Counter()

for i in task2_data['train']:
  phi_labelwvalue = i['fid'].split("\\n")
  print(phi_label)
  phi_label = [j.split(":")[0] for j in phi_labelwvalue]
  ctr.update(phi_label)

print(ctr)

['DATE']
['19']
['23']
['121']
['156']
['218']
['1000']
['1002']
['1074']
['1089']
['1092']
['1093']
['1101']
['1103']
['1159']
['1209']
['1212']
['1225']
['1307']
['1336']
['1346']
['1406']
['1444']
['1461']
['1472']
['1473']
['1482']
['1527']
['1578']
['1626']
['1633']
['1639']
['1641']
['1645']
['1773']
['1797']
['1818']
['1821']
['1834']
['1848']
['1862']
['1872']
['1894']
['1899']
['1907']
['1931']
['1933']
['1957']
['2007']
['2010']
['2017']
['2031']
['2032']
['2037']
['2043']
['2048']
['2053']
['2087']
['2107']
['2127']
['2140']
['2164']
['2175']
['2193']
['2195']
['2235']
['2296']
['2344']
['2348']
['2367']
['2372']
['2390']
['2391']
['2450']
['10004']
['10042']
['10101']
['10104']
['10120']
['10136']
['10144']
['10166']
['10168']
['10182']
['10185']
['10194']
['10203']
['10224']
['10263']
['10290']
['10300']
['10334']
['10346']
['10435']
['10444']
['10466']
['10479']
['10483']
['10494']
['10506']
['10525']
['10557']
['10558']
['10600']
['10619']
['10633']
['10644']
['10650']
[

AttributeError: 'NoneType' object has no attribute 'split'

## Model imoprt

In [ ]:
from huggingface_hub import login
    
# 輸入你的token
login(token="")

## 改良版

In [ ]:
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig, AutoConfig
import torch
from peft import prepare_model_for_kbit_training, LoraConfig, get_peft_model


task2_model_name = "suayptalha/DeepSeek-R1-Distill-Llama-3B" 

bos = '<|endoftext|>'
eos = '<|END|>'
pad = '<|pad|>'
sep = '\n\n####\n\n'

special_tokens_dict = {
    'eos_token': eos,
    'bos_token': bos,
    'pad_token': pad,
    'sep_token': sep
}
tokenizer = AutoTokenizer.from_pretrained(task2_model_name, use_fast=False, trust_remote_code=True)
tokenizer.padding_side = 'left'
num_added_toks = tokenizer.add_special_tokens(special_tokens_dict)
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_use_double_quant=True,
)

model = AutoModelForCausalLM.from_pretrained(
    task2_model_name,
    quantization_config=bnb_config,
    trust_remote_code=True
)
model.resize_token_embeddings(len(tokenizer))

model.config.pad_token_id = tokenizer.pad_token_id
model.config.bos_token_id = tokenizer.bos_token_id
model.config.eos_token_id = tokenizer.eos_token_id
model.config.sep_token_id = tokenizer.sep_token_id
model.config.output_hidden_states = False

model = prepare_model_for_kbit_training(model)

lora_config = LoraConfig(
    r=8,
    lora_alpha=32,
    target_modules=["q_proj", "v_proj","k_proj", "o_proj"],
    lora_dropout=0.05,
    bias="none",
    task_type="CAUSAL_LM"
)

model = get_peft_model(model, lora_config)

print(f"{tokenizer.pad_token}: {tokenizer.pad_token_id}")

KeyboardInterrupt: 

In [ ]:
# You are a PHI (Protected Health Information) annotator.
# When presented with a conversation or text, after the “####” delimiter, output each PHI category label that appears, one per line, using exactly the label names below (no typos or case changes):
# Available labels:
# PATIENT, DOCTOR, USERNAME, FAMILYNAME, PROFESSION,
# ROOM, DEPARTMENT, HOSPITAL, ORGANIZATION, STREET, CITY,
# DISTRICT, COUNTY, STATE, COUNTRY, ZIP, LOCATION-OTHER,
# AGE, DATE, TIME, DURATION, SET,
# PHONE, FAX, EMAIL, URL, IPADDR,
# SSN, MEDICALRECORD, HEALTHPLAN, ACCOUNT,
# LICENSE, VEHICLE, DEVICE, BIOID, IDNUM, OTHER

In [ ]:
# def collate_batch_with_prompt_template(batch, tokenizer, template =
#   """<|endoftext|>\n\n####\n\n__LABEL__ <|END|>""", IGNORED_PAD_IDX = -100):

#   texts = [template.replace("__LABEL__", data['label']).replace("__CONTENT__",
#     data['content']) for data in list(batch)]
#   #print(texts)
#   encoded_seq = tokenizer(texts, padding=True)

#   indexed_tks = torch.tensor(encoded_seq['input_ids'])
#   attention_mask = torch.tensor(encoded_seq['attention_mask'])
#   encoded_label = torch.tensor(encoded_seq['input_ids'])
#   encoded_label[encoded_label == tokenizer.pad_token_id] = IGNORED_PAD_IDX

#   return indexed_tks, encoded_label, attention_mask

In [128]:
def collate_batch_with_prompt_template(batch, tokenizer,template=f"{bos} __CONTENT__{sep}__LABEL__ {eos}",IGNORED_PAD_IDX = -100):

  texts = [template.replace("__LABEL__", data['label'].replace("\\n", "\n")).replace("__CONTENT__",
    data['content']) for data in list(batch)]
  #print(texts)
  encoded_seq = tokenizer(texts, padding=True)

  indexed_tks = torch.tensor(encoded_seq['input_ids'])
  attention_mask = torch.tensor(encoded_seq['attention_mask'])
  encoded_label = torch.tensor(encoded_seq['input_ids'])
  encoded_label[encoded_label == tokenizer.pad_token_id] = IGNORED_PAD_IDX

  return indexed_tks, encoded_label, attention_mask

In [ ]:
# import torch
# def collate_batch_with_prompt_template(batch, tokenizer, 
#         template=f"{bos} __CONTENT__ {sep} __LABEL__ {eos}",
#         IGNORED_PAD_IDX=-100):

#     texts = [
#         template
#           .replace("__CONTENT__", data["content"])
#           .replace("__LABEL__",  data["label"].replace("\\n", "\n"))
#         for data in batch
#     ]
#     #print(texts)
#     encoded = tokenizer(texts, padding=True, return_tensors="pt")

#     input_ids      = encoded["input_ids"]       # [B, L]
#     attention_mask = encoded["attention_mask"]  # [B, L]

#     labels = input_ids.clone()

#     sep_id = tokenizer.sep_token_id
#     for i in range(labels.size(0)):
#         seq = input_ids[i]
#         sep_pos = (seq == sep_id).nonzero(as_tuple=True)[0].item()
#         labels[i, : sep_pos + 1] = IGNORED_PAD_IDX

#     labels[labels == tokenizer.pad_token_id] = IGNORED_PAD_IDX


#     return input_ids, labels, attention_mask


In [129]:
from torch.utils.data import Dataset, DataLoader


train_data = list(task2_data['train'])
train_dataloader = DataLoader(train_data, batch_size=2, shuffle=False, collate_fn=lambda batch: collate_batch_with_prompt_template(batch, tokenizer))
titer = iter(train_dataloader)
tks, labels, masks= next(titer)
#print(tks.shape)
print(tks)
print(labels)
print(masks)
#print(tokenizer.decode(tks[0]))
#print(tokenizer.decode(tks[1]))
#next(iter(titer))


tensor([[128258, 128258, 128258, 128258, 128258, 128258, 128258, 128258, 128258,
         128258, 128258, 128258, 128258, 128258, 128258, 128258, 128258, 128258,
         128258, 128258, 128258, 128258, 128258, 128258, 128258, 128258, 128258,
         128258, 128258, 128258, 128258, 128258, 128258, 128258, 128258, 128258,
         128258, 128258, 128258, 128258, 128258, 128258, 128258, 128258, 128258,
         128258, 128258, 128258, 128000, 128257,   5884,    927,   5081,    315,
           2555,    430,    596,   3169,    315,   1093,    264,   2697,   4251,
           5292,    477,   9096,  10209,    311,   1120,    636,    264,   2046,
            315,   9096,     11,    358,   2846,    539,   7556,    922,  15690,
            330,     40,   2846,   2133,    311,  29960,    349,    323,  19923,
          16190,    311,    499,    323,    311,   3137,    856,   3966,    304,
           1023,  21908,   2360,     13,   4702,   7556,    922,  15714,   1131,
         128259,  11079,    

In [130]:
results = tokenizer(
    [f"{bos} Yeah, I imagine it would — sorry, go ahead. So it's supposed to work immediately, right? Yep. So we'll see if I'm productive tomorrow. I hope I'm productive today. I've actually been trying to plan. If I do the titles today, then I can do my laundry tomorrow. Right. I probably could bring my computer and do titles while I'm doing my laundry. If I was — but I won't do that.{sep}DATE:tomorrow\nDATE:today\nDate:today {eos}",
    f"{bos} I imagine it{sep}PHI:Null {eos}"]
    ,padding=True
)
print(results['attention_mask'][0])
print(results['attention_mask'][1])
print(tokenizer.decode(results['input_ids'][0]))
print(tokenizer.decode(results['input_ids'][1]))

[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
<|begin_of_text|><|endoftext|> Yeah, I imagine it would — sorry, go ahead. So it's supposed to work immediately, right? Yep. So we'll see if I'm productive tomorrow. I hope I'm productive today. I've actually been trying to plan. If I do the titles today, then I can do my laundry tomorrow. Right. I probably could bring my computer and d

In [131]:
BATCH_SIZE = 8
bucket_train_dataloader = DataLoader(train_data,
  batch_sampler=OpenDeidBatchSampler(train_data, BATCH_SIZE),
  collate_fn=lambda batch: collate_batch_with_prompt_template(batch, tokenizer),
  pin_memory=True)

In [10]:
for idx, batch in enumerate(bucket_train_dataloader):
    print(f"Batch {idx}，共 {len(batch)} 筆")
    
    for sample_idx, sample in enumerate(batch):
        print(f"Sample {sample_idx}: {sample}")



Batch 0，共 3 筆
Sample 0: tensor([[151670, 151670, 151670,  ...,   3729,    220, 151669],
        [151670, 151670, 151670,  ...,   3280,    220, 151669],
        [151670, 151670, 151670,  ...,  18787,    220, 151669],
        ...,
        [151670, 151670, 151670,  ...,   5183,    220, 151669],
        [151670, 151670, 151670,  ...,  62566,    220, 151669],
        [151670, 151670, 151670,  ...,   3951,    220, 151669]])
Sample 1: tensor([[  -100,   -100,   -100,  ...,   3729,    220, 151669],
        [  -100,   -100,   -100,  ...,   3280,    220, 151669],
        [  -100,   -100,   -100,  ...,  18787,    220, 151669],
        ...,
        [  -100,   -100,   -100,  ...,   5183,    220, 151669],
        [  -100,   -100,   -100,  ...,  62566,    220, 151669],
        [  -100,   -100,   -100,  ...,   3951,    220, 151669]])
Sample 2: tensor([[0, 0, 0,  ..., 1, 1, 1],
        [0, 0, 0,  ..., 1, 1, 1],
        [0, 0, 0,  ..., 1, 1, 1],
        ...,
        [0, 0, 0,  ..., 1, 1, 1],
        [0,

In [132]:
model.print_trainable_parameters()

trainable params: 9,175,040 || all params: 3,221,937,152 || trainable%: 0.2848


## Training

In [133]:
from transformers import get_scheduler
from tqdm import tqdm
import torch
import os

# --- Hyperparameter Configuration ---
EPOCHS = 50
GRADIENT_ACCUMULATION_STEPS = 4
LEARNING_RATE = 3e-4
MAX_GRAD_NORM = 1.0
EARLY_STOP_PATIENCE = 6
OUTPUT_DIR = r"./models/qlora_DeepSeek-R1-Distill-Llama-3B_LR3e-4_R16_TEST"  # google/gemma-3-4b-it Consistent naming meta-llama/Llama-3.2-3B-Instructmeta-llama/Meta-Llama-3-8B-Instruct meta-llama/Llama-3.2-3B
WEIGHT_DECAY = 1e-1  # Added weight decay
# --- End Hyperparameter Configuration ---
# 1E-4 0.17
os.makedirs(OUTPUT_DIR, exist_ok=True)

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)
model.train()

# --- Optimizer ---
optimizer = torch.optim.AdamW(
    model.parameters(),
    lr=LEARNING_RATE,
    weight_decay=WEIGHT_DECAY,  # Use the defined weight decay
)

# --- Learning Rate Scheduler ---
total_steps = (
    len(bucket_train_dataloader) * EPOCHS // GRADIENT_ACCUMULATION_STEPS
)  # Correct calculation
WARMUP_STEPS = int(total_steps * 0.02)   # ≈ 96
print(WARMUP_STEPS)
lr_scheduler = get_scheduler(

    "linear",
    optimizer=optimizer,
    num_warmup_steps=WARMUP_STEPS,  # Use the defined warmup steps
    num_training_steps=total_steps,
)
"""l
lr_scheduler = get_scheduler(
    "cosine_with_restarts",
    optimizer=optimizer,
    num_warmup_steps=WARMUP_STEPS,
    num_training_steps=total_steps)
"""
# --- Early Stopping ---
best_loss = float("inf")
early_stop_counter = 0
LABEL_SMOOTHING_FACTOR = 0.1

# --- Training Loop ---
for epoch in range(EPOCHS):
    total_loss = 0.0
    model.train()

    progress_bar = tqdm(enumerate(bucket_train_dataloader), total=len(bucket_train_dataloader), desc=f"Epoch {epoch+1}")

    for step, (seqs, labels, masks) in progress_bar:
        input_ids = seqs.to(device)
        labels = labels.to(device)
        attention_mask = masks.to(device)

        outputs = model(input_ids=input_ids, attention_mask=attention_mask, labels=labels)  # 不是所有模型都支援)
        loss = outputs.loss / GRADIENT_ACCUMULATION_STEPS
        loss.backward()
        total_loss += loss.item()

        if (step + 1) % GRADIENT_ACCUMULATION_STEPS == 0 or (step + 1) == len(bucket_train_dataloader):
            torch.nn.utils.clip_grad_norm_(model.parameters(), MAX_GRAD_NORM)
            optimizer.step()
            lr_scheduler.step()
            model.zero_grad()

        progress_bar.set_postfix(
            loss=loss.item() * GRADIENT_ACCUMULATION_STEPS,
            lr=lr_scheduler.get_last_lr()[0]
        )

    avg_loss = total_loss / len(bucket_train_dataloader)
    print(f"\nEpoch {epoch+1} average loss: {avg_loss:.4f}")

    # ==== save best model ====
    if avg_loss < best_loss:
        best_loss = avg_loss
        early_stop_counter = 0
        best_path = os.path.join(OUTPUT_DIR, "best_adapter")
        model.save_pretrained(best_path)
        tokenizer.save_pretrained(best_path)
        print(f"Best model saved at {best_path} with loss {avg_loss:.4f}")
    else:
        early_stop_counter += 1
        print(f"No improvement. Early stop patience: {early_stop_counter}/{EARLY_STOP_PATIENCE}")

    # ==== Early Stopping ====
    if early_stop_counter >= EARLY_STOP_PATIENCE:
        print(f"Early stopping triggered at epoch {epoch+1}. Best loss: {best_loss:.4f}")
        break  


# model.save_pretrained(OUTPUT_DIR) #save_pretrained should handle both.  If you have issues, put this back.
# tokenizer.save_pretrained(OUTPUT_DIR)




72


Epoch 1:   0%|          | 0/289 [00:00<?, ?it/s]c:\Users\mb205\anaconda3\envs\DataMining\Lib\site-packages\torch\_dynamo\eval_frame.py:838: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.5 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)
Epoch 1: 100%|██████████| 289/289 [05:03<00:00,  1.05s/it, loss=4.97, lr=0.0003]  



Epoch 1 average loss: 0.8653


c:\Users\mb205\anaconda3\envs\DataMining\Lib\site-packages\peft\utils\save_and_load.py:250: UserWarning: Setting `save_embedding_layers` to `True` as the embedding layer has been resized during finetuning.
  warnings.warn(


Best model saved at ./models/qlora_DeepSeek-R1-Distill-Llama-3B_LR3e-4_R16_TEST\best_adapter with loss 0.8653


...


Epoch 5 average loss: 1.7299
No improvement. Early stop patience: 1/6


Epoch 6: 100%|██████████| 289/289 [04:54<00:00,  1.02s/it, loss=nan, lr=0.000269]



Epoch 6 average loss: nan
No improvement. Early stop patience: 2/6


Epoch 7:   5%|▍         | 14/289 [00:16<05:29,  1.20s/it, loss=nan, lr=0.000269]


KeyboardInterrupt: 

## Load finetune model

## 改良

In [ ]:

from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig,AutoConfig
from peft import PeftModel

bos = '<|endoftext|>'
eos = '<|END|>'
pad = '<|pad|>'
sep = '\n\n####\n\n'
# bos = '<|begin_of_text|>'
# eos = '<|end_of_text|>'
# pad = '<|pad|>'
# sep = '\n\n####\n\n'

special_tokens_dict = {
    'eos_token': eos,
    'bos_token': bos,
    'pad_token': pad,
    'sep_token': sep
}
base_model_name = "suayptalha/DeepSeek-R1-Distill-Llama-3B"
adapter_path = r"./models/qlora_DeepSeek-R1-Distill-Llama-3B_LR3e-4_VER2"

tokenizer = AutoTokenizer.from_pretrained(adapter_path, trust_remote_code=True)
tokenizer.padding_side = 'left'
tokenizer.add_special_tokens(special_tokens_dict) 


bnb_config = BitsAndBytesConfig(load_in_4bit=True, bnb_4bit_quant_type="nf4", bnb_4bit_use_double_quant=True)
base_model = AutoModelForCausalLM.from_pretrained(base_model_name, quantization_config=bnb_config, trust_remote_code=True)
base_model.resize_token_embeddings(len(tokenizer))

base_model.config.pad_token_id = tokenizer.pad_token_id
base_model.config.bos_token_id = tokenizer.bos_token_id
base_model.config.eos_token_id = tokenizer.eos_token_id
base_model.config.sep_token_id = tokenizer.sep_token_id
base_model.config.output_hidden_states = False

model = PeftModel.from_pretrained(base_model, adapter_path)
model.eval().cuda()

Loading checkpoint shards: 100%|██████████| 2/2 [00:06<00:00,  3.37s/it]
The new embeddings will be initialized from a multivariate normal distribution that has old embeddings' mean and covariance. As described in this article: https://nlp.stanford.edu/~johnhew/vocab-expansion.html. To disable this, use `mean_resizing=False`


PeftModelForCausalLM(
  (base_model): LoraModel(
    (model): LlamaForCausalLM(
      (model): LlamaModel(
        (embed_tokens): Embedding(128260, 3072, padding_idx=128004)
        (layers): ModuleList(
          (0-27): 28 x LlamaDecoderLayer(
            (self_attn): LlamaAttention(
              (q_proj): lora.Linear4bit(
                (base_layer): Linear4bit(in_features=3072, out_features=3072, bias=False)
                (lora_dropout): ModuleDict(
                  (default): Dropout(p=0.05, inplace=False)
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=3072, out_features=8, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=8, out_features=3072, bias=False)
                )
                (lora_embedding_A): ParameterDict()
                (lora_embedding_B): ParameterDict()
                (lora_magnitude_vector): ModuleDict()
              )
         

## Output result

In [19]:
task2_valid_data = r"./result/TRAINGING DATASET_1PHASE/submission/task1_answer.txt"
valid_data = load_dataset("csv", data_files=task2_valid_data, delimiter='\t',
  features = Features({'fid': Value('string'),'content': Value('string')}),
  column_names=['fid', 'content'])
valid_list = list(valid_data['train'])
valid_data

DatasetDict({
    train: Dataset({
        features: ['fid', 'content'],
        num_rows: 712
    })
})

In [20]:
print(valid_data['train'][0])


{'fid': '73173', 'content': 'The patient withdrew Harkley is identified by ID number 99B-76441 and medical record 990764.ker. The report was last added on August 22, 2063. The case was handled by Dr. W. E. and Dr. Y. Nostan, with the specimen being processed on August 19, 2063.'}


In [21]:
with open(r"./result/TRAINGING DATASET_1PHASE/task1_answer_timestamps.json", 'r', encoding='utf-8') as file:
  audio_timestamps = json.load(file)

In [22]:
len(audio_timestamps)

710

In [ ]:
from collections import defaultdict
import re

train_phi_category = ['PATIENT', 'DOCTOR', 'USERNAME','FAMILYNAME','PROFESSION','PERSONALNAME',
             'ROOM', 'DEPARTMENT', 'HOSPITAL', 'ORGANIZATION', 'STREET', 'CITY',
             'DISTRICT','COUNTY','STATE', 'COUNTRY', 'ZIP', 'LOCATION-OTHER',
             'AGE',
             'DATE', 'TIME', 'DURATION', 'SET',
             'PHONE', 'FAX', 'EMAIL', 'URL', 'IPADDR',
             'SSN', 'MEDICAL_RECORD_NUMBER', 'HEALTHPLAN', 'ACCOUNT',
             'LICENSE', 'VEHICLE', 'DEVICE', 'BIOID', 'ID_NUMBER',
             'OTHER']

def detect_language(s: str) -> str:

    s = s.strip()
    if re.search(r'[A-Za-z0-9]', s) is None:
        return "chinese"
    return "english"
def split_chinese_or_mixed(s: str) -> list[str]:

    s = s.strip()
    if re.search(r'\s', s):
        return re.split(r'\s+', s)
    else:
        return list(s)
def get_anno_format(infos, audio_timestamps):
  anno_list = []
  phi_dict = defaultdict(list)
  for line in infos.split("\n"):
    if ":" not in line:
      continue
    key, value = line.split(":", 1)
    key = key.strip()
    value = value.strip()

    key,value=clean_kv(key,value)
    if((key==None)and(value==None)):
       continue
       
    if key in train_phi_category and value:
      phi_dict[key].append(value)

  remaining_timestamps = audio_timestamps.copy()
  used_indices = set()

  for phi_key, phi_values in phi_dict.items():
    for phi_value in phi_values:
      if(detect_language(phi_value)=="english"):
         phi_tokens = phi_value.lower().strip().split()
      else:
         phi_tokens = split_chinese_or_mixed(phi_value)

      for i in range(len(remaining_timestamps) - len(phi_tokens) + 1):
        if any((i + j) in used_indices for j in range(len(phi_tokens))):
          continue

        match = True
        for j, phi_token in enumerate(phi_tokens):
          tsd_word = remaining_timestamps[i + j]['word'].replace("Ġ", "").replace("▁", "").strip().lower()
          if tsd_word != phi_token:
            match = False
            break 

        if match:
          anno_list.append({
              "phi": phi_key,
              "st_time": remaining_timestamps[i]['start'],
              "ed_time": remaining_timestamps[i + len(phi_tokens) - 1]['end'],
              "entity": phi_value
          })
          for j in range(len(phi_tokens)):
            used_indices.add(i + j)
          break
  return anno_list



from collections import defaultdict

text = """<|endoftext|> __CONTENT__ \n\n####\n\n"""

def aicup_predict(model, tokenizer, _input, audio_timestamps,counterr, template = f"""{bos} __CONTENT__\n\n####\n\n"""):
  seeds = [template.replace("__CONTENT__", data['content']) for data in _input]
  sep = tokenizer.sep_token
  eos = tokenizer.eos_token
  pad = tokenizer.pad_token
  model.eval()
  device = model.device
  texts = tokenizer(seeds, return_tensors = 'pt', padding=True).to(device)
  outputs = []

  with torch.no_grad():
    output_tokens = model.generate(**texts, max_new_tokens=512, do_sample=False, 
    temperature=1.5,
    top_p=None,
    num_beams=6,
    length_penalty=0.8,       
    repetition_penalty=1.4,
    pad_token_id=tokenizer.pad_token_id,
    eos_token_id=tokenizer.eos_token_id)
    preds = tokenizer.batch_decode(output_tokens, skip_special_tokens=False)
    for idx , pred in enumerate(preds):
      pred = pred.replace("\\n", "\n")  # 把 '\\n' 換成'\n'
      #print(pred)
      if "Null" in pred:
        continue
      phi_infos = pred[pred.index(sep)+len(sep):].replace(pad, "").replace(eos, "").replace(" <|begin_of_text|>", "\n").replace(" �", "\n").replace("  And", "\n").replace(" <|start_header_id|>", "\n").replace(" <|eot_id|>", "\n").replace("  ", "\n").replace("\\", "\n").strip()
      if(counterr>250):
         print(phi_infos)
      annotations = get_anno_format(phi_infos,audio_timestamps[_input[idx]['fid']]['segments'][0]["words"])
      for annotation in annotations:
        if(counterr>250):
           print(annotation)
        outputs.append(f'{_input[idx]["fid"]}\t{annotation["phi"]}\t{annotation["st_time"]}\t{annotation["ed_time"]}\t{annotation["entity"]}')
  return outputs

In [26]:
import torch
from tqdm import tqdm
counterr=0
BATCH_SIZE = 2
outputs=None
with open(r"./result/TRAINGING DATASET_1PHASE/submission/task2_answer.txt",'w',encoding='utf8') as f:
  for i in tqdm(range(0, len(valid_list), BATCH_SIZE)):
    counterr=counterr+1
    with torch.no_grad():
      data = valid_list[i:i+BATCH_SIZE]
      outputs = aicup_predict(model, tokenizer, data, audio_timestamps, counterr)
      for o in outputs:
        f.write(o)
        f.write('\n')

  0%|          | 0/356 [00:00<?, ?it/s]c:\Users\mb205\anaconda3\envs\DataMining\Lib\site-packages\transformers\generation\configuration_utils.py:631: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `1.4` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
 71%|███████   | 251/356 [2:45:06<1:09:23, 39.65s/it]

DATE:a day
DURATION:a day
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donovan
PATIENT:Donova

 71%|███████   | 252/356 [2:45:45<1:08:44, 39.66s/it]

DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:Washington
DOCTOR:Wilson
DOCTOR:W

 71%|███████   | 253/356 [2:46:25<1:08:06, 39.67s/it]

...

PATIENT:Donita Sarabia
DATE:June 10, 1988
ID_NUMBER:13TO23532U
ID_NUMBER_NUMBER:13TO2353
ID_NUMBER_NUMBER:13TO2353
MEDICAL_RECORD_NUMBER:1370235.KHU
STREET:Bush Pound
CITY:Harvey Bay
STATE:QLD
ZIP:3111
PATIENT:Donita Sarabia
PATIENT:Donita Sarabia
DATE:June 10, 1988
ID_NUMBER:13TO23532U
ID_NUMBER_NUMBER:13TO2353
ID_NUMBER_NUMBER:13TO2353
MEDICAL_RECORD_NUMBER:1370235.KHU
STREET:Bush Pound
CITY:Harvey Bay
STATE:QLD
ZIP:3111
PATIENT:Donita Sarabia
PATIENT:Donita Sarabia
DATE:June 10, 1988
ID_NUMBER:13TO23532U
ID_NUMBER_NUMBER:13TO2353
ID_NUMBER_NUMBER:13TO2353
MEDICAL_RECORD_NUMBER:1370235.KHU
STREET:Bush Pound
CITY:Harvey Bay
STATE:QLD
ZIP:3111
PATIENT:Donita Sarabia
PATIENT:Donita Sarabia
DATE:June 10, 1988
ID_NUMBER:13TO23532U
ID_NUMBER_NUMBER:13TO2353
ID_NUMBER_NUMBER:13TO2353
MEDICAL_RECORD_NUMBER:1370235.KHU
STREET:Bush Pound
CITY:Harvey Bay
STATE:QLD
ZIP:3111
PATIENT:Donita Sarabia
PATIENT:Donita Sarabia
DATE:June 10, 1988
ID_NUMBER:13TO23532U
ID_NUMBER_NUMBER:13TO2353
ID_NUMBER_N

100%|█████████▉| 355/356 [3:53:54<00:39, 39.62s/it]

DURATION:final
DATE:final
DATE:final
DATE:final
DURATION:final
DURATION:final
DURATION:final
DATE:final
DATE:final
DATE:final
DURATION:final
DURATION:final
DURATION:final
DATE:final
DATE:final
DATE:final
DURATION:final
DURATION:final
DURATION:final
DATE:final
DATE:final
DATE:final
DURATION:final
DURATION:final
DURATION:final
DATE:final
DATE:final
DATE:final
DURATION:final
DURATION:final
DURATION:final
DATE:final
DATE:final
DATE:final
DURATION:final
DURATION:final
DURATION:final
DATE:final
DATE:final
DATE:final
DURATION:final
DURATION:final
DURATION:final
DATE:final
DATE:final
DATE:final
DURATION:final
DURATION:final
DURATION:final
DATE:final
DATE:final
DATE:final
DURATION:final
DURATION:final
DURATION:final
DATE:final
DATE:final
DATE:final
DURATION:final
DURATION:final
DURATION:final
DATE:final
DATE:final
DATE:final
DURATION:final
DURATION:final
DURATION:final
DATE:final
DATE:final
DATE:final
DURATION:final
DURATION:final
DURATION:final
DATE:final
DATE:final
DATE:final
DURATION:final
D

100%|██████████| 356/356 [3:54:33<00:00, 39.53s/it]

DEPARTMENT:Gaira Multipurpose Service
DOCTOR:Hamilton
DOCTOR:Dennis
DATE:July 17, 2062
DOCTOR:Sexton
DOCTOR:Anderson
PATIENT:Dennis
DATE:pivotal date
DATE:July 17, 2062
DOCTOR:Hamilton
DOCTOR:Dennis
DOCTOR:Sexton
DOCTOR:Anderson
PATIENT:Dennis
DATE:pivotal date
DATE:July 17, 2062
DOCTOR:Hamilton
DOCTOR:Dennis
DOCTOR:Sexton
DOCTOR:Anderson
PATIENT:Dennis
DATE:pivotal date
DATE:July 17, 2062
DOCTOR:Hamilton
DOCTOR:Dennis
DOCTOR:Sexton
DOCTOR:Anderson
PATIENT:Dennis
DATE:pivotal date
DATE:July 17, 2062
DOCTOR:Hamilton
DOCTOR:Dennis
DOCTOR:Sexton
DOCTOR:Anderson
PATIENT:Dennis
DATE:pivotal date
DATE:July 17, 2062
DOCTOR:Hamilton
DOCTOR:Dennis
DOCTOR:Sexton
DOCTOR:Anderson
PATIENT:Dennis
DATE:pivotal date
DATE:July 17, 2062
DOCTOR:Hamilton
DOCTOR:Dennis
DOCTOR:Sexton
DOCTOR:Anderson
PATIENT:Dennis
DATE:pivotal date
DATE:July 17, 2062
DOCTOR:Hamilton
DOCTOR:Dennis
DOCTOR:Sexton
DOCTOR:Anderson
PATIENT:Dennis
DATE:pivotal date
DATE:July 17, 2062
DOCTOR:Hamilton
DOCTOR:Dennis
DOCTOR:Sexton
DOC